In [3]:
!pip install --quiet sentencepiece==0.1.94
!pip install transformers
!pip install datasets
import json
import torch
from transformers import T5ForConditionalGeneration, T5Tokenizer
from datasets import Dataset, load_metric

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [4]:
import torch
from transformers import T5ForConditionalGeneration, T5Tokenizer
from datasets import load_dataset, load_metric



In [5]:

dataset = load_dataset('tydiqa', 'secondary_task')

Reusing dataset tydiqa (/home/ani/.cache/huggingface/datasets/tydiqa/secondary_task/1.0.0/b8a6c4c0db10bf5703d7b36645e5dbae821b8c0e902dac9daeecd459a8337148)


  0%|          | 0/2 [00:00<?, ?it/s]

In [6]:
print(dataset['train'])

Dataset({
    features: ['id', 'title', 'context', 'question', 'answers'],
    num_rows: 49881
})


In [7]:
for example in dataset['train']:
    print(example['id'][0:7])

finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish
finnish


In [8]:
english_examples = [example for example in dataset['train'] if example['id'][0:7] == 'english']
print(english_examples)


[{'id': 'english--9041575374418655524-12', 'title': 'Quantum field theory', 'context': 'Quantum field theory naturally began with the study of electromagnetic interactions, as the electromagnetic field was the only known classical field as of the 1920s.[8]:1', 'question': 'When was quantum field theory developed?', 'answers': {'text': ['1920s'], 'answer_start': [159]}}, {'id': 'english-1971662537536642354-0', 'title': 'List of Nobel laureates in Literature', 'context': "The Nobel Prize in Literature (Swedish: Nobelpriset i litteratur) is awarded annually by the Swedish Academy to authors for outstanding contributions in the field of literature. It is one of the five Nobel Prizes established by the 1895 will of Alfred Nobel, which are awarded for outstanding contributions in chemistry, physics, literature, peace, and physiology or medicine.[1] As dictated by Nobel's will, the award is administered by the Nobel Foundation and awarded by a committee that consists of five members elected b

In [9]:
print(len(english_examples))

3696


In [10]:
english_examples_val = [example for example in dataset['validation'] if example['id'][0:7] == 'english']
print(english_examples_val)


[{'id': 'english--3215621880858840488-2', 'title': 'Wound healing', 'context': "Wound care encourages and speeds wound healing via cleaning and protection from reinjury or infection. Depending on each patient's needs, it can range from the simplest first aid to entire nursing specialties such as wound, ostomy, and continence nursing and burn center care.", 'question': 'What is a way to increase your wound healing speed?', 'answers': {'text': ['Wound care'], 'answer_start': [0]}}, {'id': 'english-5888115353945373749-2', 'title': 'Burntisland Shipbuilding Company', 'context': 'Brothers Amos and Wilfrid Ayre founded Burntisland Shipbuilding Co. in 1918 as a First World War emergency shipyard.[1] Its yard at Burntisland West Dock had four berths and capacity to build ships up to 450 feet (140m) long[1] and up to 59 feet (18m) beam.[3] However, until the 1950s Burntisland built relatively few vessels more than about 425 feet (130m) long and 57 feet (17.4m) beam.[3]', 'question': 'Who founde

In [78]:
for a in english_examples:
    print(a['question'])

When was quantum field theory developed?
Who was the first Nobel prize winner for Literature?
When is the dialectical method used?
Who invented Hangul?
What do Grasshoppers eat?
How large is the Kerman province of southeastern Iran?
When was Guitar Hero Live first released?
When were bluebonnets named the state flower of Texas?
Who created the series Clannad?
When was the USS Taylor built?
What's the difference between man-slaughter and homicide?
When did DC comics first introduce the Guardians of the Universe?
What is the largest parrot in New Zealand?
When was the first Assassin's Creed released?
What percentage of the Earth's atmosphere is oxygen?
When was the X-Men cartoon television series first aired?
When was the Battle of Suoi Chau Pha fought?
How old was Cho Namchul when he died?
What is the Navy's military mascot?
How many permanent members of the United Nations Security Council are there?
Who created the Gundam animated series?
How long has Lucha Libre been around?
When was 

In [12]:
# Convert the SQUAD dataset to a Hugging Face Dataset object
def convert_to_dataset(data):
    dataset = {"context": [], "question": [], "answers": []}
    for article in data:
        question = article["question"]
        context = article["context"]
        dataset["context"].append(context)
        dataset["question"].append(question)
        dataset["answers"].append(article['answers']["text"])
    return Dataset.from_dict(dataset)

In [79]:
dataset_train = convert_to_dataset(english_examples)
dataset_valid = convert_to_dataset(english_examples_val)

# Define the prompts
prompts = [
    "Context: [CONTEXT] Question: [QUESTION]",
]


In [27]:

# Load the T5 model and tokenizer
# Load the T5 model and tokenizer
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = T5ForConditionalGeneration.from_pretrained('t5-base').to(device)
tokenizer = T5Tokenizer.from_pretrained('t5-base')


/home/ani/anaconda3/lib/python3.9/site-packages/transformers/models/t5/tokenization_t5.py:163: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-base automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  warnings.warn(


In [82]:
print(dataset_train)

Dataset({
    features: ['context', 'question', 'answers'],
    num_rows: 3696
})


In [43]:
for example in dataset_train:
    print(example)

{'context': 'Quantum field theory naturally began with the study of electromagnetic interactions, as the electromagnetic field was the only known classical field as of the 1920s.[8]:1', 'question': 'When was quantum field theory developed?', 'answers': ['1920s']}
{'context': "The Nobel Prize in Literature (Swedish: Nobelpriset i litteratur) is awarded annually by the Swedish Academy to authors for outstanding contributions in the field of literature. It is one of the five Nobel Prizes established by the 1895 will of Alfred Nobel, which are awarded for outstanding contributions in chemistry, physics, literature, peace, and physiology or medicine.[1] As dictated by Nobel's will, the award is administered by the Nobel Foundation and awarded by a committee that consists of five members elected by the Swedish Academy.[2] The first Nobel Prize in Literature was awarded in 1901 to Sully Prudhomme of France.[3] Each recipient receives a medal, a diploma and a monetary award prize that has vari

In [80]:
# Generate the input-output pairs
pairs = []
batch_size = 4
for i in range(0, 3696, batch_size):
    batch = dataset_train[i:i+batch_size]
    for j in range(0,batch_size):
        for prompt in prompts:
            input_text = prompt.replace("[CONTEXT]", batch['context'][j])
            input_text = input_text.replace("[QUESTION]", batch['question'][j])
            target_text = batch['answers'][j][0]
            input_ids = tokenizer.encode(input_text, max_length=512, return_tensors='pt')
            target_ids = tokenizer.encode(target_text, max_length=512, return_tensors='pt')
            pairs.append((input_ids, target_ids))
            

In [81]:
def train(pairs, model, tokenizer, num_epochs=1, print_every=100):
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    model = model.to(device)
    optimizer = torch.optim.AdamW(model.parameters(), lr=5e-5)

    for epoch in range(num_epochs):
        print('Epoch:', epoch+1)
        for i, pair in enumerate(pairs):
            input_ids, target_ids = pair
            input_ids = input_ids.to(device)
            target_ids = target_ids.to(device)

            # Run the model forward to generate the logits
            logits = model(input_ids=input_ids, labels=target_ids).logits

            # Compute the loss and backpropagate
            loss = torch.nn.functional.cross_entropy(logits.view(-1, logits.size(-1)), target_ids.view(-1))
            loss.backward()
            optimizer.step()
            optimizer.zero_grad()

            if i % print_every == 0:
                print('Batch:', i, 'Loss:', loss.item())

In [82]:
train(pairs, model, tokenizer, num_epochs=3, print_every=10)

Epoch: 1
Batch: 0 Loss: 0.02389216236770153
Batch: 10 Loss: 0.028238169848918915
Batch: 20 Loss: 0.0033869845792651176
Batch: 30 Loss: 0.025992315262556076
Batch: 40 Loss: 0.007331178989261389
Batch: 50 Loss: 0.005832037888467312
Batch: 60 Loss: 0.03993852064013481
Batch: 70 Loss: 0.01214077789336443
Batch: 80 Loss: 0.00044003676157444715
Batch: 90 Loss: 0.26529911160469055
Batch: 100 Loss: 0.009286323562264442
Batch: 110 Loss: 0.01063273474574089
Batch: 120 Loss: 0.09958180040121078
Batch: 130 Loss: 0.09451647102832794
Batch: 140 Loss: 0.033322691917419434
Batch: 150 Loss: 0.30814164876937866
Batch: 160 Loss: 0.01921861432492733
Batch: 170 Loss: 0.06461837887763977
Batch: 180 Loss: 0.02289128303527832
Batch: 190 Loss: 0.06871312111616135
Batch: 200 Loss: 0.1866782009601593
Batch: 210 Loss: 0.30267196893692017
Batch: 220 Loss: 0.09123869985342026
Batch: 230 Loss: 0.001759655773639679
Batch: 240 Loss: 0.0002256562002003193
Batch: 250 Loss: 0.001709930133074522
Batch: 260 Loss: 1.1542314

In [83]:
# Load the SQUAD evaluation dataset and metric
eval_dataset = dataset_valid
metric = load_metric('squad')

# Generate predictions and compute metrics
j=0
predictions = []
for example in eval_dataset:
    input_text = prompts[0].replace("[CONTEXT]", example['context'])
    input_text = input_text.replace("[QUESTION]", example['question'])
    input_ids = tokenizer.encode(input_text, return_tensors='pt')
    output_ids = model.generate(input_ids)
    output_text = tokenizer.decode(output_ids[0], skip_special_tokens=True)
    predictions.append(output_text)

/home/ani/anaconda3/lib/python3.9/site-packages/transformers/generation/utils.py:1313: UserWarning: Using `max_length`'s default (20) to control the generation length. This behaviour is deprecated and will be removed from the config in v5 of Transformers -- we recommend using `max_new_tokens` to control the maximum length of the generation.


In [84]:
references=[example['answers'] for example in eval_dataset]

In [85]:
print(len(predictions))

440


In [86]:
references=references[0:440]

In [87]:
def normalize_text(s):
    """Removing articles and punctuation, and standardizing whitespace are all typical text processing steps."""
    import string, re

    def remove_articles(text):
        regex = re.compile(r"\b(a|an|the)\b", re.UNICODE)
        return re.sub(regex, " ", text)

    def white_space_fix(text):
        return " ".join(text.split())

    def remove_punc(text):
        exclude = set(string.punctuation)
        return "".join(ch for ch in text if ch not in exclude)

    def lower(text):
        return text.lower()

    return white_space_fix(remove_articles(remove_punc(lower(s))))

def compute_exact_match(prediction, truth):
    return int(normalize_text(prediction) == normalize_text(truth))

def compute_f1(prediction, truth):
    pred_tokens = normalize_text(prediction).split()
    truth_tokens = normalize_text(truth).split()
    
    # if either the prediction or the truth is no-answer then f1 = 1 if they agree, 0 otherwise
    if len(pred_tokens) == 0 or len(truth_tokens) == 0:
        return int(pred_tokens == truth_tokens)
    
    common_tokens = set(pred_tokens) & set(truth_tokens)
    
    # if there are no common tokens then f1 = 0
    if len(common_tokens) == 0:
        return 0
    
    prec = len(common_tokens) / len(pred_tokens)
    rec = len(common_tokens) / len(truth_tokens)
    
    return 2 * (prec * rec) / (prec + rec)

def get_gold_answers(example):
    """helper function that retrieves all possible true answers from a squad2.0 example"""
    
    gold_answers = [answer["text"] for answer in example.answers if answer["text"]]

    # if gold_answers doesn't exist it's because this is a negative example - 
    # the only correct answer is an empty string
    if not gold_answers:
        gold_answers = [""]
        
    return gold_answers

In [88]:
avg_em=0
avg_f1=0
for i in range(len(predictions)):
    gold_answers = references[i]
    em_score = max((compute_exact_match(predictions[i], answer)) for answer in gold_answers)
    f1_score = max((compute_f1(predictions[i], answer)) for answer in gold_answers)
    avg_em+=em_score
    avg_f1+=f1_score

avg_em=avg_em/len(predictions)
avg_f1=avg_f1/len(predictions)
print(f"EM: {avg_em} \t F1: {avg_f1}")

EM: 0.5545454545454546 	 F1: 0.6847118974632608


Zero-Shot Learning

In [89]:
finnish_examples_val = [example for example in dataset['validation'] if example['id'][0:7] == 'finnish']
dataset_valid_fn = convert_to_dataset(finnish_examples_val)

In [90]:
print(finnish_examples_val)

[{'id': 'finnish--267686407665346253-29', 'title': 'Lasi', 'context': 'Vanhin tunnettu lasilaatu on alkali\xadkalkki\xadlasi, jota valmistetaan soodan, hiekan ja kalkin seoksesta. Egyptissä siitä valmistettiin lasitettuja kivi\xadhelmiä jo noin vuonna 4000 eaa.[8] Jo varhain havaittiin, että lasi voitiin saada värilliseksi lisäämällä siihen eri malmeja. Tällaista värillistä lasia käytettiin keramiikan lasitukseen sekä jalokivien jäljitelmiin.[8]', 'question': 'Kauanko lasia on valmistettu?', 'answers': {'text': ['vuonna 4000 eaa', '4000 eaa'], 'answer_start': [165, 172]}}, {'id': 'finnish--1940328803600511418-0', 'title': 'Ponzi-huijaus', 'context': 'Ponzi-huijaus eli Ponzi-järjestelmä on pyramidihuijauksen muoto, jossa joku kerää pääomia kuviteltua tai olemassa olevaa sijoituskohdetta varten luvaten sijoituksille nopeaa ja korkeaa tuottoa: korkeampaa kuin mistään muusta sijoitustoiminnasta on mahdollista saada. Sijoituskohde voi olla kultavaranto, kaivos, öljyesiintymä, lomaosake tai 

In [91]:
# Load the SQUAD evaluation dataset and metric
eval_dataset = dataset_valid_fn
metric = load_metric('squad')

In [92]:
print(eval_dataset[0])

{'context': 'Vanhin tunnettu lasilaatu on alkali\xadkalkki\xadlasi, jota valmistetaan soodan, hiekan ja kalkin seoksesta. Egyptissä siitä valmistettiin lasitettuja kivi\xadhelmiä jo noin vuonna 4000 eaa.[8] Jo varhain havaittiin, että lasi voitiin saada värilliseksi lisäämällä siihen eri malmeja. Tällaista värillistä lasia käytettiin keramiikan lasitukseen sekä jalokivien jäljitelmiin.[8]', 'question': 'Kauanko lasia on valmistettu?', 'answers': ['vuonna 4000 eaa', '4000 eaa']}


In [93]:
# Generate predictions and compute metrics
j=0
predictions = []
for example in eval_dataset:
    j=j+1
    if(j>100):
        break
    input_text = prompts[0].replace("[CONTEXT]", example['context'])
    input_text = input_text.replace("[QUESTION]", example['question'])
    input_ids = tokenizer.encode(input_text, return_tensors='pt')
    output_ids = model.generate(input_ids)
    output_text = tokenizer.decode(output_ids[0], skip_special_tokens=True)
    predictions.append(output_text)

In [94]:
print(predictions)

['jota valmistettaan soodan, hie', 'eli Ponzi-järjestelmä on pyramidihuijauk', 'Sotien jälkeen Ranska alistettiin kovilla', 'Kokemäenjoki () on Satakunnan ja Pirkanma', 'eli tahdosta riippumaton hermost', 'teoriaansa', '– 26. elokuuta 1979 Helsinki', 'kaarevan järvi. Järven pituus saa', 'joulukuussa 1872', 'pidettiin Sveitsin Luganossa vuonna 1956', 'viljelijä A. Forselv vuonna 1929', '671', 'oli yhdysvallat – 8. kesäkuu', 'Kebnekaise (saam. Giebmegáisi', 'kaikkiaan 1895', 'lähteä sotakouluun', 'PC Kid', 'osaksi elektroniset musiikkite', 'käytiin Suomen ja Neuvostoliittoon', 'energianlähteinä ja kemianteollisuudes', 'Venäjän keisarikunta () oli Euroopan itä', 'oli genovalainen oli kruunu', 'joka sai idean sarjan luomiseen', 'elokuvaa, joista teatterielokuvia Back to the US', 'oli Beringinmerelle ulottunut keisarikunta', '& Nartun 6', 'Lapuan liike (joskus lapuanliike)', 'tai ADoM', 'elokuvassaan Big and Liggle Wong Tin Bar', 'valtatiet ot 20–30 kilometrin päähän kaup', 'Saksasta vuosie

In [95]:
references=[example['answers'] for example in eval_dataset]

In [96]:
references=references[0:100]

In [97]:
def normalize_text(s):
    """Removing articles and punctuation, and standardizing whitespace are all typical text processing steps."""
    import string, re

    def remove_articles(text):
        regex = re.compile(r"\b(a|an|the)\b", re.UNICODE)
        return re.sub(regex, " ", text)

    def white_space_fix(text):
        return " ".join(text.split())

    def remove_punc(text):
        exclude = set(string.punctuation)
        return "".join(ch for ch in text if ch not in exclude)

    def lower(text):
        return text.lower()

    return white_space_fix(remove_articles(remove_punc(lower(s))))

def compute_exact_match(prediction, truth):
    return int(normalize_text(prediction) == normalize_text(truth))

def compute_f1(prediction, truth):
    pred_tokens = normalize_text(prediction).split()
    truth_tokens = normalize_text(truth).split()
    
    # if either the prediction or the truth is no-answer then f1 = 1 if they agree, 0 otherwise
    if len(pred_tokens) == 0 or len(truth_tokens) == 0:
        return int(pred_tokens == truth_tokens)
    
    common_tokens = set(pred_tokens) & set(truth_tokens)
    
    # if there are no common tokens then f1 = 0
    if len(common_tokens) == 0:
        return 0
    
    prec = len(common_tokens) / len(pred_tokens)
    rec = len(common_tokens) / len(truth_tokens)
    
    return 2 * (prec * rec) / (prec + rec)

def get_gold_answers(example):
    """helper function that retrieves all possible true answers from a squad2.0 example"""
    
    gold_answers = [answer["text"] for answer in example.answers if answer["text"]]

    # if gold_answers doesn't exist it's because this is a negative example - 
    # the only correct answer is an empty string
    if not gold_answers:
        gold_answers = [""]
        
    return gold_answers

In [98]:
avg_em=0
avg_f1=0
for i in range(len(predictions)):
    gold_answers = references[i]
    em_score = max((compute_exact_match(predictions[i], answer)) for answer in gold_answers)
    f1_score = max((compute_f1(predictions[i], answer)) for answer in gold_answers)
    avg_em+=em_score
    avg_f1+=f1_score

avg_em=avg_em/len(predictions)
avg_f1=avg_f1/len(predictions)
print(f"EM: {avg_em} \t F1: {avg_f1}")

EM: 0.01 	 F1: 0.14250484155313378


Few-Shot Learning

In [99]:
finnish_examples_train = [example for example in dataset['train'] if example['id'][0:7] == 'finnish']
dataset_train_fn = convert_to_dataset(finnish_examples_train)

In [100]:
# Generate the input-output pairs
pairs = []
batch_size = 4
for i in range(0, 250, batch_size):
    batch = dataset_train_fn[i:i+batch_size]
    for j in range(0,batch_size):
        for prompt in prompts:
            input_text = prompt.replace("[CONTEXT]", batch['context'][j])
            input_text = input_text.replace("[QUESTION]", batch['question'][j])
            target_text = batch['answers'][j][0]
            input_ids = tokenizer.encode(input_text, max_length=512, return_tensors='pt')
            target_ids = tokenizer.encode(target_text, max_length=512, return_tensors='pt')
            pairs.append((input_ids, target_ids))

In [101]:
print(len(pairs))

252


In [102]:
train(pairs, model, tokenizer, num_epochs=2, print_every=10)

Epoch: 1
Batch: 0 Loss: 0.3256046175956726
Batch: 10 Loss: 0.7061150074005127
Batch: 20 Loss: 0.3312050998210907
Batch: 30 Loss: 0.5118378400802612
Batch: 40 Loss: 0.2909872233867645
Batch: 50 Loss: 0.5301383137702942
Batch: 60 Loss: 1.3046621084213257
Batch: 70 Loss: 0.13930264115333557
Batch: 80 Loss: 1.2184401750564575
Batch: 90 Loss: 0.1889323890209198
Batch: 100 Loss: 0.7059261798858643
Batch: 110 Loss: 0.44450151920318604
Batch: 120 Loss: 0.35860660672187805
Batch: 130 Loss: 0.05372554063796997
Batch: 140 Loss: 0.4330257773399353
Batch: 150 Loss: 0.4976981282234192
Batch: 160 Loss: 0.1515556126832962
Batch: 170 Loss: 0.5380496978759766
Batch: 180 Loss: 0.04560624063014984
Batch: 190 Loss: 0.014819473028182983
Batch: 200 Loss: 0.18926048278808594
Batch: 210 Loss: 0.8371278047561646
Batch: 220 Loss: 0.4273087978363037
Batch: 230 Loss: 0.35798773169517517
Batch: 240 Loss: 1.173391342163086
Batch: 250 Loss: 0.6240654587745667
Epoch: 2
Batch: 0 Loss: 0.11729210615158081
Batch: 10 Loss

In [103]:
# Load the SQUAD evaluation dataset and metric
eval_dataset = dataset_valid_fn
metric = load_metric('squad')

In [104]:
# Generate predictions and compute metrics
j=0
predictions = []
for example in eval_dataset:
    j=j+1
    if(j>100):
        break
    input_text = prompts[0].replace("[CONTEXT]", example['context'])
    input_text = input_text.replace("[QUESTION]", example['question'])
    input_ids = tokenizer.encode(input_text, return_tensors='pt')
    output_ids = model.generate(input_ids)
    output_text = tokenizer.decode(output_ids[0], skip_special_tokens=True)
    predictions.append(output_text)

In [105]:
references=[example['answers'] for example in eval_dataset]
references=references[0:100]

In [106]:
avg_em=0
avg_f1=0
for i in range(len(predictions)):
    gold_answers = references[i]
    em_score = max((compute_exact_match(predictions[i], answer)) for answer in gold_answers)
    f1_score = max((compute_f1(predictions[i], answer)) for answer in gold_answers)
    avg_em+=em_score
    avg_f1+=f1_score

avg_em=avg_em/len(predictions)
avg_f1=avg_f1/len(predictions)
print(f"EM: {avg_em} \t F1: {avg_f1}")

EM: 0.32 	 F1: 0.43749567099567094
